# Imports

In [1]:
import pandas as pd 
import requests 
from bs4 import BeautifulSoup
import numpy as np 
from urllib.parse import urljoin
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import TimeoutException
import time

# Reading the Web Site

In [2]:
url = 'https://www.imdb.com/search/title/?release_date=2012-01-02,2013-01-02&genres=!documentary,!short&count=250'
headers = {'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/58.0.3029.110 Safari/537.3'}

In [3]:
response = requests.get(url, headers=headers)

soup = BeautifulSoup(response.content, 'html.parser')

In [4]:
print(soup)

<!DOCTYPE html>
<html lang="en-US" xmlns:fb="http://www.facebook.com/2008/fbml" xmlns:og="http://opengraphprotocol.org/schema/"><head><meta charset="utf-8"/><meta content="width=device-width" name="viewport"/><script>if(typeof uet === 'function'){ uet('bb', 'LoadTitle', {wb: 1}); }</script><script>window.addEventListener('load', (event) => {
        if (typeof window.csa !== 'undefined' && typeof window.csa === 'function') {
            var csaLatencyPlugin = window.csa('Content', {
                element: {
                    slotId: 'LoadTitle',
                    type: 'service-call'
                }
            });
            csaLatencyPlugin('mark', 'clickToBodyBegin', 1714722560890);
        }
    })</script><title>Advanced search</title><meta content="" data-id="main" name="description"/><meta content="https://www.imdb.com/search/" property="og:url"/><meta content="IMDb" property="og:site_name"/><meta content="Advanced search" property="og:title"/><meta content="" property=

In [5]:
#storing the meaningfull required data in the variable
movie_data = soup.findAll('div', attrs= {'class': 'ipc-metadata-list-summary-item__c'})

In [6]:
movie_data

[<div class="ipc-metadata-list-summary-item__c"><div class="ipc-metadata-list-summary-item__tc"><span aria-disabled="false" class="ipc-metadata-list-summary-item__t"></span><div class="sc-74bf520e-3 klvfeN dli-parent"><div class="sc-74bf520e-2 cVXqoq"><div class="sc-e5a25b0f-0 jQjDIb dli-poster-container"><div class="ipc-poster ipc-poster--base ipc-poster--dynamic-width ipc-sub-grid-item ipc-sub-grid-item--span-2" role="group"><div aria-label="add to watchlist" class="ipc-watchlist-ribbon ipc-focusable ipc-watchlist-ribbon--s ipc-watchlist-ribbon--base ipc-watchlist-ribbon--loading ipc-watchlist-ribbon--onImage ipc-poster__watchlist-ribbon" role="button" tabindex="0"><svg class="ipc-watchlist-ribbon__bg" height="34px" role="presentation" viewbox="0 0 24 34" width="24px" xmlns="http://www.w3.org/2000/svg"><polygon class="ipc-watchlist-ribbon__bg-ribbon" fill="#000000" points="24 0 0 0 0 32 12.2436611 26.2926049 24 31.7728343"></polygon><polygon class="ipc-watchlist-ribbon__bg-hover" poi

# Scrap the Web Site

In [3]:
#creating an empty list, so that we can append the values
movie_name = []
year = []
rating = []
metascore = []
imdp_score = []
imdp_votes = []
gross = []
budget = []
description = []
Director = []
Stars = []
production = []
language = []
location =[]

# Initialize the Firefox WebDriver (make sure geckodriver is in your PATH)
driver = webdriver.Chrome()
i = 0
try:
    # Navigate to the web page containing the button
    driver.get('https://www.imdb.com/search/title/?release_date=2012-01-02,2013-01-02&genres=!documentary,!short&count=250')
    while i < 5:
        # Wait for the "50 more" button to be clickable (using its class name)
        button = WebDriverWait(driver, 10).until(EC.element_to_be_clickable((By.CLASS_NAME, "ipc-see-more__text")))

        # Scroll to the button (optional)
        driver.execute_script("arguments[0].scrollIntoView();", button)

        # Trigger the button's click event using JavaScript
        driver.execute_script("arguments[0].click();", button)

        time.sleep(3)

        i += 1 
        
except TimeoutException:
    print("Button not found or not clickable")

finally:
    # Get the page source after clicking all "See More" buttons
    page_source = driver.page_source
    
    

    # Parse the page source using BeautifulSoup
    soup = BeautifulSoup(page_source, 'html.parser')

movie_data = soup.findAll('div', attrs= {'class': 'ipc-metadata-list-summary-item__c'})    

for store in movie_data:
    plist = []
    Llist = []
    FLlist = []

    name = store.h3.text
    movie_name.append(name)
    
    meta  = store.find('span', class_ = 'sc-b0901df4-0 bcQdDJ metacritic-score-box').text.replace(' ', '') if store.find('span', class_ = 'sc-b0901df4-0 bcQdDJ metacritic-score-box') else 'nan'
    metascore.append(meta)
    
    # Find the div containing all the metadata items
    metadata_div = store.div

    # Find all spans within the metadata div
    metadata_spans = metadata_div.find_all('span', class_='sc-b189961a-8 kLaxqf dli-title-metadata-item')

    # Extract year of release from the first span
    if len(metadata_spans) >= 1:
        year_of_release = metadata_spans[0].text.replace('(', '').replace(')', '')
        year.append(year_of_release)

    

    # Extract the text from the span
    imdp_s = store.div.find('span', class_='ipc-rating-star ipc-rating-star--base ipc-rating-star--imdb ratingGroup--imdb-rating')

    if imdp_s:

        imdp_s = imdp_s.text

        # Split the string to separate the score and the number of votes
        imdp_parts = imdp_s.split('(')

        # Extract the IMDb score
        imdb_score = imdp_parts[0].strip()

        # Extract the number of votes
        votes = imdp_parts[1].replace(')', '').strip()
    else:
        imdb_score = np.nan
        votes = np.nan

    # Append the IMDb score and the number of votes to their respective lists
    imdp_score.append(imdb_score)
    imdp_votes.append(votes)

    #Append the description
    desc = store.find('div', class_='ipc-html-content-inner-div')

    if desc:

        description.append(desc.text.strip())

    else:
        description.append(np.nan)


    # Find the anchor tag containing the movie name
    movie_anchor = store.find('a', class_='ipc-title-link-wrapper')  # Replace 'your-movie-class' with the actual class of the anchor tag

    # Extract the href attribute value
    movie_href = movie_anchor['href']

    # Join the relative URL with the base URL to get the full URL
    full_url = urljoin('https://www.imdb.com/', movie_href)
    print(full_url)
    
    # Send a request to the full URL
    response = requests.get(full_url, headers=headers)
    soup = BeautifulSoup(response.content, 'html.parser')

    # Extract director information
    director = soup.find('a', class_='ipc-metadata-list-item__list-content-item ipc-metadata-list-item__list-content-item--link')
    if director:
        Director.append(director.text.strip())
    else:
        Director.append(np.nan)

    # Find all the <a> elements containing the actors' names based on data-testid attribute
    actor_links = soup.find_all('a', attrs={'data-testid': 'title-cast-item__actor'})
    
    if actor_links:
        # Extract the text from each <a> element containing actor names and store in a list
        cast_list = [actor_link.text.strip() for actor_link in actor_links]
        
    else:

        cast_list = np.nan
        

    Stars.append(cast_list)
    
    
    divBox = soup.find('div', attrs={'data-testid':"title-boxoffice-section"})
    
    if divBox:
        # Find all spans within the metadata div
        divboxnames = divBox.find_all('span', class_='ipc-metadata-list-item__label')
        budgetdata_spans = divBox.find_all('span', class_='ipc-metadata-list-item__list-content-item')

        div = 0
        gross_numeric = np.nan
        budget_numeric = np.nan

        for div in range(len(divboxnames)):
            if divboxnames[div].text == 'Budget':
                gross_text = budgetdata_spans[div].text.strip()
                # Extract only the numerical value
                budget_numeric = ''.join(filter(str.isdigit, gross_text))

            if divboxnames[div].text == 'Gross worldwide':
                world = divBox.find('li',attrs={'data-testid':"title-boxoffice-cumulativeworldwidegross"})
                gross_text = world.find(class_='ipc-metadata-list-item__list-content-item').text.strip()
                # Extract only the numerical value
                gross_numeric = ''.join(filter(str.isdigit, gross_text))

        gross.append(gross_numeric)
        budget.append(budget_numeric)
    else:
        budget.append(np.nan)
        gross.append(np.nan)
            

    detailsdev = soup.find('div' , attrs={'data-testid' :'title-details-section'})

    detailsname = detailsdev.findAll(class_='ipc-metadata-list-item__label')
    
    details = detailsdev.findAll('div' , class_='ipc-metadata-list-item__content-container')

    x = 0
    

    prodCom = np.nan
    lang = np.nan
    loc = np.nan
    for x in range(len(detailsname)):
        
        if detailsname[x].text == 'Production companies':
            moredetails = details[x].findAll(class_='ipc-metadata-list-item__list-content-item ipc-metadata-list-item__list-content-item--link')
            p = 0
            for p in range(len(moredetails)):
                plist.append(moredetails[p].text.strip())
            prodCom = plist

        if detailsname[x].text == 'Language' or detailsname[x].text == 'Languages':
            moredetails = details[x].findAll(class_='ipc-metadata-list-item__list-content-item ipc-metadata-list-item__list-content-item--link')
            l = 0
            for l in range(len(moredetails)):
                Llist.append(moredetails[l].text.strip())
            lang = Llist

        if detailsname[x].text == 'Filming locations':
            moredetails = details[x].findAll(class_='ipc-metadata-list-item__list-content-item ipc-metadata-list-item__list-content-item--link')
            fl = 0
            for fl in range(len(moredetails)):
                FLlist.append(moredetails[fl].text.strip())
            loc = FLlist

    production.append(prodCom)
    language.append(lang)
    location.append(loc)

    
# Close the browser window
driver.quit()

https://www.imdb.com/title/tt2261391/?ref_=sr_t_1
https://www.imdb.com/title/tt1983079/?ref_=sr_t_2
https://www.imdb.com/title/tt1392170/?ref_=sr_t_3
https://www.imdb.com/title/tt1853728/?ref_=sr_t_4
https://www.imdb.com/title/tt1232200/?ref_=sr_t_5
https://www.imdb.com/title/tt2193021/?ref_=sr_t_6
https://www.imdb.com/title/tt1695360/?ref_=sr_t_7
https://www.imdb.com/title/tt2191671/?ref_=sr_t_8
https://www.imdb.com/title/tt1345836/?ref_=sr_t_9
https://www.imdb.com/title/tt2303687/?ref_=sr_t_10
https://www.imdb.com/title/tt1723816/?ref_=sr_t_11
https://www.imdb.com/title/tt1837576/?ref_=sr_t_12
https://www.imdb.com/title/tt1446714/?ref_=sr_t_13
https://www.imdb.com/title/tt1232829/?ref_=sr_t_14
https://www.imdb.com/title/tt0903624/?ref_=sr_t_15
https://www.imdb.com/title/tt0848228/?ref_=sr_t_16
https://www.imdb.com/title/tt2701582/?ref_=sr_t_17
https://www.imdb.com/title/tt1371111/?ref_=sr_t_18
https://www.imdb.com/title/tt1981677/?ref_=sr_t_19
https://www.imdb.com/title/tt1759761/?re

https://www.imdb.com/title/tt1714204/?ref_=sr_t_161
https://www.imdb.com/title/tt2290065/?ref_=sr_t_162
https://www.imdb.com/title/tt1602620/?ref_=sr_t_163
https://www.imdb.com/title/tt2498968/?ref_=sr_t_164
https://www.imdb.com/title/tt1797404/?ref_=sr_t_165
https://www.imdb.com/title/tt1985443/?ref_=sr_t_166
https://www.imdb.com/title/tt1989475/?ref_=sr_t_167
https://www.imdb.com/title/tt0337692/?ref_=sr_t_168
https://www.imdb.com/title/tt0431021/?ref_=sr_t_169
https://www.imdb.com/title/tt1535438/?ref_=sr_t_170
https://www.imdb.com/title/tt1769363/?ref_=sr_t_171
https://www.imdb.com/title/tt1366365/?ref_=sr_t_172
https://www.imdb.com/title/tt1555093/?ref_=sr_t_173
https://www.imdb.com/title/tt1591479/?ref_=sr_t_174
https://www.imdb.com/title/tt1819509/?ref_=sr_t_175
https://www.imdb.com/title/tt2023453/?ref_=sr_t_176
https://www.imdb.com/title/tt1496025/?ref_=sr_t_177
https://www.imdb.com/title/tt1763264/?ref_=sr_t_178
https://www.imdb.com/title/tt1949012/?ref_=sr_t_179
https://www.

https://www.imdb.com/title/tt1788453/?ref_=sr_t_319
https://www.imdb.com/title/tt1510686/?ref_=sr_t_320
https://www.imdb.com/title/tt1885102/?ref_=sr_t_321
https://www.imdb.com/title/tt1821681/?ref_=sr_t_322
https://www.imdb.com/title/tt1937449/?ref_=sr_t_323
https://www.imdb.com/title/tt1956017/?ref_=sr_t_324
https://www.imdb.com/title/tt2330866/?ref_=sr_t_325
https://www.imdb.com/title/tt2004262/?ref_=sr_t_326
https://www.imdb.com/title/tt2369037/?ref_=sr_t_327
https://www.imdb.com/title/tt2103264/?ref_=sr_t_328
https://www.imdb.com/title/tt2006848/?ref_=sr_t_329
https://www.imdb.com/title/tt0404978/?ref_=sr_t_330
https://www.imdb.com/title/tt2094064/?ref_=sr_t_331
https://www.imdb.com/title/tt1866570/?ref_=sr_t_332
https://www.imdb.com/title/tt1799834/?ref_=sr_t_333
https://www.imdb.com/title/tt1650048/?ref_=sr_t_334
https://www.imdb.com/title/tt1935896/?ref_=sr_t_335
https://www.imdb.com/title/tt2085930/?ref_=sr_t_336
https://www.imdb.com/title/tt1047540/?ref_=sr_t_337
https://www.

https://www.imdb.com/title/tt1733582/?ref_=sr_t_477
https://www.imdb.com/title/tt2027128/?ref_=sr_t_478
https://www.imdb.com/title/tt1934205/?ref_=sr_t_479
https://www.imdb.com/title/tt2040560/?ref_=sr_t_480
https://www.imdb.com/title/tt2250064/?ref_=sr_t_481
https://www.imdb.com/title/tt2180809/?ref_=sr_t_482
https://www.imdb.com/title/tt2269368/?ref_=sr_t_483
https://www.imdb.com/title/tt1990314/?ref_=sr_t_484
https://www.imdb.com/title/tt1910605/?ref_=sr_t_485
https://www.imdb.com/title/tt2050633/?ref_=sr_t_486
https://www.imdb.com/title/tt2557948/?ref_=sr_t_487
https://www.imdb.com/title/tt1870372/?ref_=sr_t_488
https://www.imdb.com/title/tt2039399/?ref_=sr_t_489
https://www.imdb.com/title/tt1975249/?ref_=sr_t_490
https://www.imdb.com/title/tt1930546/?ref_=sr_t_491
https://www.imdb.com/title/tt2202488/?ref_=sr_t_492
https://www.imdb.com/title/tt2368518/?ref_=sr_t_493
https://www.imdb.com/title/tt2114184/?ref_=sr_t_494
https://www.imdb.com/title/tt1745686/?ref_=sr_t_495
https://www.

https://www.imdb.com/title/tt2216577/?ref_=sr_t_635
https://www.imdb.com/title/tt2328749/?ref_=sr_t_636
https://www.imdb.com/title/tt1951218/?ref_=sr_t_637
https://www.imdb.com/title/tt1995329/?ref_=sr_t_638
https://www.imdb.com/title/tt1024770/?ref_=sr_t_639
https://www.imdb.com/title/tt2139843/?ref_=sr_t_640
https://www.imdb.com/title/tt2078523/?ref_=sr_t_641
https://www.imdb.com/title/tt2339647/?ref_=sr_t_642
https://www.imdb.com/title/tt1981140/?ref_=sr_t_643
https://www.imdb.com/title/tt0938305/?ref_=sr_t_644
https://www.imdb.com/title/tt1855401/?ref_=sr_t_645
https://www.imdb.com/title/tt1640218/?ref_=sr_t_646
https://www.imdb.com/title/tt1867093/?ref_=sr_t_647
https://www.imdb.com/title/tt1901040/?ref_=sr_t_648
https://www.imdb.com/title/tt2239947/?ref_=sr_t_649
https://www.imdb.com/title/tt1911553/?ref_=sr_t_650
https://www.imdb.com/title/tt1059836/?ref_=sr_t_651
https://www.imdb.com/title/tt2782216/?ref_=sr_t_652
https://www.imdb.com/title/tt2231696/?ref_=sr_t_653
https://www.

https://www.imdb.com/title/tt2181931/?ref_=sr_t_793
https://www.imdb.com/title/tt2400129/?ref_=sr_t_794
https://www.imdb.com/title/tt2112293/?ref_=sr_t_795
https://www.imdb.com/title/tt2227610/?ref_=sr_t_796
https://www.imdb.com/title/tt2308725/?ref_=sr_t_797
https://www.imdb.com/title/tt2357249/?ref_=sr_t_798
https://www.imdb.com/title/tt2208216/?ref_=sr_t_799
https://www.imdb.com/title/tt3003738/?ref_=sr_t_800
https://www.imdb.com/title/tt2224455/?ref_=sr_t_801
https://www.imdb.com/title/tt1735862/?ref_=sr_t_802
https://www.imdb.com/title/tt1799508/?ref_=sr_t_803
https://www.imdb.com/title/tt2226301/?ref_=sr_t_804
https://www.imdb.com/title/tt1608368/?ref_=sr_t_805
https://www.imdb.com/title/tt2293276/?ref_=sr_t_806
https://www.imdb.com/title/tt1870529/?ref_=sr_t_807
https://www.imdb.com/title/tt2375255/?ref_=sr_t_808
https://www.imdb.com/title/tt1959409/?ref_=sr_t_809
https://www.imdb.com/title/tt2317337/?ref_=sr_t_810
https://www.imdb.com/title/tt2798620/?ref_=sr_t_811
https://www.

https://www.imdb.com/title/tt1559036/?ref_=sr_t_951
https://www.imdb.com/title/tt2122954/?ref_=sr_t_952
https://www.imdb.com/title/tt2246837/?ref_=sr_t_953
https://www.imdb.com/title/tt1758610/?ref_=sr_t_954
https://www.imdb.com/title/tt1865346/?ref_=sr_t_955
https://www.imdb.com/title/tt2417490/?ref_=sr_t_956
https://www.imdb.com/title/tt2724814/?ref_=sr_t_957
https://www.imdb.com/title/tt2889186/?ref_=sr_t_958
https://www.imdb.com/title/tt1863352/?ref_=sr_t_959
https://www.imdb.com/title/tt1612782/?ref_=sr_t_960
https://www.imdb.com/title/tt2439946/?ref_=sr_t_961
https://www.imdb.com/title/tt2388350/?ref_=sr_t_962
https://www.imdb.com/title/tt2163913/?ref_=sr_t_963
https://www.imdb.com/title/tt1728986/?ref_=sr_t_964
https://www.imdb.com/title/tt2476828/?ref_=sr_t_965
https://www.imdb.com/title/tt2874064/?ref_=sr_t_966
https://www.imdb.com/title/tt2402623/?ref_=sr_t_967
https://www.imdb.com/title/tt1641975/?ref_=sr_t_968
https://www.imdb.com/title/tt2402600/?ref_=sr_t_969
https://www.

https://www.imdb.com/title/tt2323894/?ref_=sr_t_1107
https://www.imdb.com/title/tt0980999/?ref_=sr_t_1108
https://www.imdb.com/title/tt2010976/?ref_=sr_t_1109
https://www.imdb.com/title/tt2093073/?ref_=sr_t_1110
https://www.imdb.com/title/tt1928329/?ref_=sr_t_1111
https://www.imdb.com/title/tt2392143/?ref_=sr_t_1112
https://www.imdb.com/title/tt2234717/?ref_=sr_t_1113
https://www.imdb.com/title/tt2205948/?ref_=sr_t_1114
https://www.imdb.com/title/tt2113822/?ref_=sr_t_1115
https://www.imdb.com/title/tt2215395/?ref_=sr_t_1116
https://www.imdb.com/title/tt2176353/?ref_=sr_t_1117
https://www.imdb.com/title/tt1540767/?ref_=sr_t_1118
https://www.imdb.com/title/tt2180333/?ref_=sr_t_1119
https://www.imdb.com/title/tt2236642/?ref_=sr_t_1120
https://www.imdb.com/title/tt2647078/?ref_=sr_t_1121
https://www.imdb.com/title/tt2005164/?ref_=sr_t_1122
https://www.imdb.com/title/tt1921070/?ref_=sr_t_1123
https://www.imdb.com/title/tt2175509/?ref_=sr_t_1124
https://www.imdb.com/title/tt1906347/?ref_=sr_

# Save as CSV File

In [4]:
#creating a dataframe using pandas library
movieDF2012 = pd.DataFrame({'movie_name': movie_name, 'relase_year': year, 'Metascore': metascore, 'imdb_votes': imdp_votes, 'imdb_score': imdp_score,'gross_collection': gross, 'Budget': budget, 'Description': description, "Director": Director, 'Actor': Stars, 'Production_companies': production, "Languages": language, 'Film_location': location})

In [6]:
#Saving data in Excel file:
movieDF2012.to_csv("IMDB_Movies2012.csv")

In [5]:
movieDF2012.head(63)

movie_name relase_year Metascore imdb_votes imdb_score  \
0       1. Chicago Fire      2012–        nan        65K        8.0   
1   2. Call the Midwife      2012–        nan        32K        8.6   
2   3. The Hunger Games        2012        68         1M        7.2   
3   4. Django Unchained        2012        81       1.7M        8.5   
4      5. That's My Boy        2012        31       109K        5.5   
..                  ...         ...       ...        ...        ...   
58       59. Life of Pi        2012        79       667K        7.9   
59    60. Anna Karenina        2012        63       107K        6.6   
60       61. The Master        2012        86       186K        7.1   
61        62. The Lorax        2012        46       130K        6.4   
62   63. Wreck-It Ralph        2012        72       459K        7.7   

   gross_collection     Budget  \
0               NaN        NaN   
1               NaN        NaN   
2         695220619   78000000   
3         426076293  100000000   
4          57719093   70000000   
..              ...        ...   
58        609016565  120000000   
59         68929150   40600000   
60         28288071   32000000   
61        349305397   70000000   
62        471222889  165000000   

                                          Description              Director  \
0   The story of firefighters and paramedics in th...        Michael Brandt   
1   Chronicles the lives of a group of midwives li...          Heidi Thomas   
2   Katniss Everdeen voluntarily takes her younger...             Gary Ross   
3   With the help of a German bounty-hunter, a fre...     Quentin Tarantino   
4   While in his teens, Donny fathered a son, Todd...           Sean Anders   
..                                                ...                   ...   
58  A young man who survives a disaster at sea is ...               Ang Lee   
59  In late-19th-century Russian high society, St....            Joe Wright   
60  A Naval veteran arrives home from war unsettle...  Paul Thomas Anderson   
61  A 12-year-old boy searches for the one thing t...          Chris Renaud   
62  A video game villain wants to be a hero and se...            Rich Moore   

                                                Actor  \
0   [Taylor Kinney, Christian Stolte, Eamonn Walke...   
1   [Vanessa Redgrave, Laura Main, Jenny Agutter, ...   
2   [Jennifer Lawrence, Josh Hutcherson, Liam Hems...   
3   [Jamie Foxx, Christoph Waltz, Leonardo DiCapri...   
4   [Adam Sandler, Andy Samberg, Leighton Meester,...   
..                                                ...   
58  [Suraj Sharma, Irrfan Khan, Adil Hussain, Tabu...   
59  [Keira Knightley, Jude Law, Aaron Taylor-Johns...   
60  [Joaquin Phoenix, Philip Seymour Hoffman, Amy ...   
61  [Zac Efron, Taylor Swift, Danny DeVito, Ed Hel...   
62  [John C. Reilly, Jack McBrayer, Jane Lynch, Sa...   

                                 Production_companies  \
0                  [Wolf Films, Universal Television]   
1   [Neal Street Productions, British Broadcasting...   
2                      [Lionsgate Films, Color Force]   
3          [The Weinstein Company, Columbia Pictures]   
4   [Columbia Pictures, Happy Madison Productions,...   
..                                                ...   
58  [Fox 2000 Pictures, Dune Entertainment, Ingeni...   
59  [Universal Pictures, Focus Features, Working T...   
60  [The Weinstein Company, Ghoulardi Film Company...   
61  [Universal Pictures, Illumination Entertainmen...   
62  [Walt Disney Animation Studios, Walt Disney Pi...   

                             Languages  \
0                            [English]   
1                            [English]   
2                            [English]   
3   [English, German, French, Italian]   
4                            [English]   
..                                 ...   
58  [English, Hindi, Japanese, French]   
59                           [English]   
60                 [English, Filipino]   
61          